# Example of Pythonic Motion Planning (pymp)

Github: https://github.com/Jiayuan-Gu/pymp

This is an example to use `pymp` to plan a path for the Franka Panda robot (7-DoF arm) to pick and place an object.

## Install dependencies

**Please restart the colab runtime after installing dependencies.**

In [1]:
!pip install --upgrade numpy scipy
!pip install motion-planning[meshcat]
!pip uninstall -y pathlib  # avoid overriding builtin one 

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 21.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.5/34.5 MB 36.0 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 1.21.6
    Uninstalling numpy-1.21.6:
      Successfully uninstalled numpy-1.21.6
  Attempting uninstall: scipy
    Found existing installation: scipy 1.7.3
    Uninstalling scipy-1.7.3:
      Successfully uninstalled scipy-1.7.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
numba 0.56.4 requires numpy<1.24,>=1.18, but you have numpy 1.24.1 which is incompatible.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.1/6.1 MB 70.7 MB/s eta 0:00:

## Donwload necessary data

In [2]:
# For colab
!git clone https://github.com/Jiayuan-Gu/pymp --single-branch --depth 1
!mv pymp/data data

Cloning into 'pymp'...
remote: Enumerating objects: 59, done.
remote: Counting objects: 100% (59/59), done.
remote: Compressing objects: 100% (56/56), done.
remote: Total 59 (delta 0), reused 46 (delta 0), pack-reused 0
Unpacking objects: 100% (59/59), done.


## Example: Pick-and-Place

### Import packages

In [1]:
import os
import time

import numpy as np
import pinocchio as pin

from pymp import Planner, toSE3

<frozen importlib._bootstrap>:219: RuntimeWarning: to-Python converter for std::shared_ptr<hpp::fcl::CollisionGeometry> already registered; second conversion method ignored.


In [2]:
# Show supported pose formats
print(toSE3.__doc__)

Convert to pinocchio.SE3

    Args:
        x: input pose. See notes for supported formats.

    Returns:
        pinocchio.SE3

    Notes:
        We support the following formats:
        - xyz: [3] for position
        - wijk: [4] for quaternion
        - xyzwijk: [7] for position and quaternion
        - T: [4, 4], rigid transformation
        - sapien: sapien.Pose, which has p and q
    


### Initialize Planner

In [3]:
# Create planner
urdf = os.path.join("data/panda.urdf")
planner = Planner(
    urdf,
    None,
    ee_link_name="panda_hand_tcp",
    timestep=0.1,
    joint_vel_limits=1,
    joint_acc_limits=1,
)


# Initial joint positions
init_qpos = np.array([0, 0.2, 0.0, -2.62, 0.0, 2.94, 0.785, 0.04, 0.04])

# Initial end-effector pose
init_ee_pose = planner.scene.framePlacement(init_qpos, "panda_hand_tcp")

# Initialize environment
planner.scene.addBox([0.04, 0.04, 0.12], toSE3([0.7, 0, 0.06]), name="box")
planner.scene.addBox(
    [0.1, 0.4, 0.2], toSE3([0.55, 0, 0.1]), color=(0, 1, 1, 1), name="obstacle"
)

2023-01-13 09:08:13,305 - pymp.planner - INFO - No SRDF provided. Use SRDF at data/panda.srdf.


### Visualization (Meshcat)

In [4]:
# Initialize visualizer
from pinocchio.visualize import MeshcatVisualizer

try:
    viz = MeshcatVisualizer(
        planner.scene.model,
        collision_model=planner.scene.collision_model,
        visual_model=planner.scene.visual_model,
    )
    viz.initViewer()
    viz.loadViewerModel()
except ImportError as err:
    print("Install Meshcat for visualization: `pip install meshcat`")
    raise err

You can open the visualizer by visiting the following URL:
http://127.0.0.1:7000/static/


In [5]:
# Implement play function for colab
from meshcat.animation import Animation

def play(visualizer, q_trajectory, dt):
  # https://github.com/rdeits/meshcat-python/blob/master/examples/animation_demo.ipynb
  anim = Animation()
  viewer = visualizer.viewer
  for k in range(q_trajectory.shape[1]):
    with anim.at_frame(viewer, k * dt) as frame:
      visualizer.viewer = frame
      visualizer.display(q_trajectory[:, k])
  
  # `set_animation` actually sends the animation to the
  # viewer. By default, the viewer will play the animation
  # right away. To avoid that, you can also pass `play=false`. 
  visualizer.viewer = viewer
  visualizer.viewer.set_animation(anim)
  return anim

In [6]:
# Visualize initial qpos
viz.display(init_qpos)
viz.viewer.render_static()

### Inverse Kinematics (IK)

In [7]:
# Goal end-effector pose
p = [0.7, 0, 0.1]
q = [0, 1, 0, 0]  # wxyz

# Compute IK
ik_results = planner.compute_CLIK([p, q], init_qpos, max_trials=20, seed=0)
print("# IK solutions:", len(ik_results))

# IK solutions: 6


In [8]:
play(viz, ik_results.T, dt=30)
viz.viewer.render_static()

### RRT-Connect path planning

In [9]:
# Use RRT-connect to plan a path
plan_result = planner.plan_birrt([p, q], init_qpos, seed=1024)
q_traj = plan_result["position"]  # [N, nq]
# Add gripper positions to trajectory
q_traj = np.pad(q_traj, [(0, 0), (0, 2)], constant_values=init_qpos[-2:])

In [10]:
# Visualize planned trajectory
play(viz, q_traj.T, dt=2)
viz.viewer.render_static()

### Attach the grasped object

In [11]:
# Attach box
last_qpos = q_traj[-1]
box2world = planner.scene.getGeometry("box").placement
frame2world = planner.scene.framePlacement(last_qpos, "panda_hand_tcp")
box2frame = frame2world.inverse() * box2world
planner.scene.attachBox([0.04, 0.04, 0.12], box2frame, "panda_hand_tcp")

# Remove the previous box
# planner.scene.disableCollision("box")
viz.delete(planner.scene.getGeometry("box"), pin.GeometryType.VISUAL)
planner.scene.removeGeometry("box")

In [12]:
# Planning group can be modified
planner.planning_group = planner.user_joint_names
# If planning group is changed, you need to change joint vel and acc limits.
# Here, we just disable time parameterization
planner.timestep = None
plan_result = planner.plan_birrt(init_ee_pose, last_qpos, seed=1024)
q_traj = plan_result["position"]

In [13]:
# Visualize planned trajectory
viz.reload(planner.scene.getGeometry("attached_box"), pin.GeometryType.VISUAL)
play(viz, q_traj.T, dt=2)
viz.viewer.render_static()